# Backtest vectorizado y optimización de parametros con Pandas.

## Hackeado by J3viton (learning BackTesting 2021).

---

En este Notebook vamos a realizar un backtest de una estrategia sencilla. Se trata de un cruce de medias, que se puede considerar el "Hello World!" de los sistemas automáticos.

Vamos a usar el módulo Pandas, para realizar un backtest vectorizado, es decir calcular el resultado del backtest sin iterar sobre las filas (barras) de la serie temporal.

Posteriormente realizarmos una optimización de los parametros del sistema, y veremos como el calculo vectorizador nos permite hacer un gran número de backtests para la optimización en un tiempo muy breve.

---

# IMPORTACIÓN DE MODULOS Y CARGA DE DATOS


Como es usual, importamos los módulos que vamos a necesitar para las distintas tareas, y preparamos Matplotlib para una mejor visualización de los gráficos en el notebook.

Se importa un modulo llamado **analisis**, en realidad se trata de un archivo .py con algunas funciones de apoyo para el trabajo, debe estar guardado en la misma carpeta que este notebook.

In [1]:
import pandas as pd
import analisis   
import numpy as np
import itertools
import seaborn as sns
import yfinance as yf

%matplotlib inline
import matplotlib.pyplot as plt
plt.rcParams['figure.figsize'] = 18, 8
plt.style.use('ggplot')

from IPython.display import display, Markdown

Importamos el modulo **quandl** que nos proporcionará una descarga de los datos que vamos a necesitar, en este caso la cotización diaria de las acciones de Apple.  

In [2]:
# import quandl
# quandl.ApiConfig.api_key = "Aquí va tu API KEY" # Para una descarga ocasional no necesitas la API KEY.
# qd_data = quandl.get("WIKI/AAPL", start_date= "2000-01-01", end_date= "2018-06-15")

qd_data = yf.download('MTS.MC', '2015-1-1','2021-1-1')

[*********************100%***********************]  1 of 1 completed


Tambien puedes cargar los datos desde el archivo pickle.

In [3]:
# qd_data = pd.read_pickle('apple_qd.pkl')

Veamos la cabecera del dataframe que acabamos de crear con los datos descargados.

In [4]:
qd_data.head()

Open       High        Low      Close  Adj Close  Volume
Date                                                                     
2015-01-02  18.666080  18.892052  18.313890  18.340355  17.308126  571717
2015-01-05  18.279282  18.466574  17.629868  17.650225  16.656839  584564
2015-01-06  17.739799  18.051273  17.576937  17.646154  16.652998  428394
2015-01-07  17.788658  18.026846  17.530113  17.627832  16.635708  440488
2015-01-08  17.756086  18.324068  17.713335  18.293531  17.263939  525319

La tabla muestra que tenemos datos sin ajustar y ajustados. Tomaremos solo los datos OHLCV ajustados y el volumen, prescindiremos del resto de columnas, y eliminaremos el prefijo __Adj.__ para mas comodidad de uso.

Estudiar las posibildades de Python en vectorizado ...

In [5]:
ajustadas = [f for f in qd_data.columns if f.startswith('Adj')]  # guardamos una lista con las cabeceras de las columnas
qd_data = qd_data[ajustadas].copy()    # guardamos la tabla con las cabeceras selecionas arriba
qd_data.columns = [f[4:] for f in qd_data.columns]  #quitamos los literales
qd_data.head()

Close
Date                 
2015-01-02  17.308126
2015-01-05  16.656839
2015-01-06  16.652998
2015-01-07  16.635708
2015-01-08  17.263939

Para usarlo en nuestro backtest vamos a hacer una copia del dataframe pero solo hasta 2017.

In [6]:
data = qd_data[:-1].copy()

In [7]:
data.head()

Close
Date                 
2015-01-02  17.308126
2015-01-05  16.656839
2015-01-06  16.652998
2015-01-07  16.635708
2015-01-08  17.263939

---


# DEFINICION DEL SISTEMA

Es importante tener clara la lógica del sistema, pues debemos plasmarla de forma sencilla y correcta en el dataframe para realizar el backtest del mismo.

Esta estrategia utiliza dos medias simples del precio de cierre, de 20 y 60 periodos. Calculemoslas y asignamos sus valores a nuevas columnas de nuestro dataframe.

Para ello usamos la función **rolling** de Pandas, que va _rodando_ una ventana de N valores, sobre la que realiza un calculo, en este caso la media.
https://github.com/Python-para-Trading/Webinars-Docs/blob/master/Webinar%202/Webinar%202%20-%20Backtest%20con%20Pandas%20v%202.ipynb.

In [8]:
import analisis
import regresionAMedia_v2 as rg
import pandas as pd
import datetime as dt
from time import time

{'can_join_groups': True, 'first_name': 'vital_bot', 'supports_inline_queries': False, 'can_read_all_group_messages': False, 'username': 'vital_quant_bot', 'id': 1473252352, 'is_bot': True}


In [9]:
# Rango completo para backTesting
start2 =dt.datetime(2005,1,2)
end2   =dt.datetime(2021,11,18)
start_G= start2.strftime("%Y-%m-%d")
end_G  =   end2.strftime("%Y-%m-%d")
TOTAL_len= (end2-start2).days
print('Tamaño timeseries a analizar:  ', TOTAL_len, 'sesiones')

#ventana de analisis 200 sesiones
startWindow2 =dt.datetime(2010,1,5)
endWindow2   =startWindow2 + dt.timedelta(days=200) 
startWindow= startWindow2.strftime("%Y-%m-%d")
endWindow  =   endWindow2.strftime("%Y-%m-%d")
window_len= (endWindow2-startWindow2).days
print('Tamaño de la ventana a analizar paso a paso:  ', window_len, 'sesiones')

Tamaño timeseries a analizar:   6164 sesiones
Tamaño de la ventana a analizar paso a paso:   200 sesiones


In [10]:
 #dff = pd.DataFrame(columns=('Close','Volume', 'Senal', 'Dif_Close', 'Retornos','Capital'))



In [11]:
instrumento = 'IBE.MC'

In [12]:
dff = yf.download(instrumento, start_G,end_G)

[*********************100%***********************]  1 of 1 completed


In [13]:
#dff['Close']= Total_data['Close']
#dff.dropna(inplace=True)  
dff.head()

Open    High     Low   Close  Adj Close    Volume
Date                                                           
2005-01-03  4.6000  4.6300  4.5650  4.6225   2.124916  17417636
2005-01-04  4.6350  4.6650  4.6175  4.6500   2.137558  86410008
2005-01-05  4.6400  4.6400  4.5825  4.6000   2.114573  91434776
2005-01-06  4.6000  4.6000  4.6000  4.6000   2.114573         0
2005-01-07  4.5875  4.6275  4.5875  4.6275   2.127215  91201856

In [14]:
regreMedia= rg.StrategyClass()    #Creamos la clase

In [15]:
#recogo = regreMedia.analisis_IN('MTS.MC', startWindow, endWindow, dff)
#type(recogo)

### Miro si el resultado de la estrategia me da la señal de compra (100) y lo marco en la tabla
if(recogo['senal'] == 100 ):
    dff.loc[[start],['Senal']]=100
else:
    dff.loc[[start],['Senal']]=1

dff.head()
dff.tail()

## 4.- Recorremos el datafrema con valores buscando las señales de la estrategia

In [16]:
dff.index


DatetimeIndex(['2005-01-03', '2005-01-04', '2005-01-05', '2005-01-06',
               '2005-01-07', '2005-01-10', '2005-01-11', '2005-01-12',
               '2005-01-13', '2005-01-14',
               ...
               '2021-11-04', '2021-11-05', '2021-11-08', '2021-11-09',
               '2021-11-10', '2021-11-11', '2021-11-12', '2021-11-15',
               '2021-11-16', '2021-11-17'],
              dtype='datetime64[ns]', name='Date', length=4318, freq=None)

start ='2010-1-5'
#dff.loc[start] 
if((start in dff.index)and(end in dff.index)) :
    print('si')
    

In [17]:
#dff.loc[[endWindow],['Close']]


# Proceso de backTesting
En este 'for' vamos recorriendo la muestra del historico de datos (TOTAL), desplaznado una sesion hacia el futuro 
en cada iteracion. Marcamos en la columna 'senal' las entradas como 100.

In [18]:
startWindow


'2010-01-05'

In [19]:
tiempo_inicial = time() 

In [20]:
dfe = pd.DataFrame({'A' : []})   #df empty

In [23]:
for i in range(TOTAL_len):
    endWindow3   =endWindow2 + dt.timedelta(days=i) 
    endWindow    =endWindow3.strftime("%Y-%m-%d")
    print ('end date:', endWindow)
    
    if(endWindow in dff.index):
        df_aux= dff.loc[startWindow:endWindow]    #voy pasando los datos desplazando la ventana
        recogo = regreMedia.analisis_IN(instrumento, startWindow, endWindow, df_aux) #Llamada a la clase estrategia. LA CLAVE DE TODO!!!
        print ('.............Analizando, muestra', i, 'fecha', endWindow)
        if(recogo['senal'] == 1 ):
            dff.loc[[endWindow],['Senal']]= 1
        elif(recogo['senal'] == 0 ):
            dff.loc[[endWindow],['Senal']]= 0
        elif(recogo['senal'] == -1 ):
            dff.loc[[endWindow],['Senal']]= -1            
        elif(recogo['senal'] == 503 ):
            dff.loc[[endWindow],['Senal']]= 0          
            
    else:
        print('..............Día sin sesión, next please')

        

end date: 2010-07-24
..............Día sin sesión, next please
end date: 2010-07-25
..............Día sin sesión, next please
end date: 2010-07-26
 datos desde archivo
Coefficients: 
 [-0.0113299]
Independent term: 
 6.619031474723682
Coefficients: 
 [-0.0113299]
Independent term: 
 6.619031474723682
DataFrame is empty!
  instrumento  long_short_out       date   precio
0      IBE.MC               0 2021-06-28   9.3340
1      ACX.MC               1 2021-09-22  10.9200
2      SAN.MC               1 2021-09-22   2.8995
3      TEF.MC               1 2021-09-22   4.0520
4      MTS.MC               1 2021-09-22  24.6700
5      MAP.MC               1 2021-09-22   1.7740
6     BBVA.MC               1 2021-09-22   5.2810
.............Analizando, muestra 2 fecha 2010-07-26
end date: 2010-07-27
 datos desde archivo
Coefficients: 
 [-0.01120888]
Independent term: 
 6.613303261744108
Coefficients: 
 [-0.01120888]
Independent term: 
 6.613303261744108
DataFrame is empty!
  instrumento  long_short_ou

C:\Users\INNOVACION\Documents\J3\100.- cursos\Quant_udemy\programas\Projects\regresionLineal_MediaMovil\quant_j3_lib.py:825: FutureWarning: As the xlwt package is no longer maintained, the xlwt engine will be removed in a future version of pandas. This is the only engine in pandas that supports writing in the xls format. Install openpyxl and write to an xlsx file instead. You can set the option io.excel.xls.writer to 'xlwt' to silence this warning. While this option is deprecated and will also raise a warning, it can be globally set and the warning suppressed.
  sheet_name="data")
C:\Users\INNOVACION\Documents\J3\100.- cursos\Quant_udemy\programas\Projects\regresionLineal_MediaMovil\quant_j3_lib.py:825: FutureWarning: As the xlwt package is no longer maintained, the xlwt engine will be removed in a future version of pandas. This is the only engine in pandas that supports writing in the xls format. Install openpyxl and write to an xlsx file instead. You can set the option io.excel.xls.w

end date: 2010-07-31
..............Día sin sesión, next please
end date: 2010-08-01
..............Día sin sesión, next please
end date: 2010-08-02
 datos desde archivo
Coefficients: 
 [-0.01068392]
Independent term: 
 6.587998100229211
Coefficients: 
 [-0.01068392]
Independent term: 
 6.587998100229211
DataFrame is empty!
  instrumento  long_short_out       date   precio
0      IBE.MC               0 2021-06-28   9.3340
1      ACX.MC               1 2021-09-22  10.9200
2      SAN.MC               1 2021-09-22   2.8995
3      TEF.MC               1 2021-09-22   4.0520
4      MTS.MC               1 2021-09-22  24.6700
5      MAP.MC               1 2021-09-22   1.7740
6     BBVA.MC               1 2021-09-22   5.2810
.............Analizando, muestra 9 fecha 2010-08-02
end date: 2010-08-03
 datos desde archivo
Coefficients: 
 [-0.01051742]
Independent term: 
 6.579839469730453
Coefficients: 
 [-0.01051742]
Independent term: 
 6.579839469730453
DataFrame is empty!
  instrumento  long_short_

C:\Users\INNOVACION\Documents\J3\100.- cursos\Quant_udemy\programas\Projects\regresionLineal_MediaMovil\quant_j3_lib.py:825: FutureWarning: As the xlwt package is no longer maintained, the xlwt engine will be removed in a future version of pandas. This is the only engine in pandas that supports writing in the xls format. Install openpyxl and write to an xlsx file instead. You can set the option io.excel.xls.writer to 'xlwt' to silence this warning. While this option is deprecated and will also raise a warning, it can be globally set and the warning suppressed.
  sheet_name="data")
C:\Users\INNOVACION\Documents\J3\100.- cursos\Quant_udemy\programas\Projects\regresionLineal_MediaMovil\quant_j3_lib.py:825: FutureWarning: As the xlwt package is no longer maintained, the xlwt engine will be removed in a future version of pandas. This is the only engine in pandas that supports writing in the xls format. Install openpyxl and write to an xlsx file instead. You can set the option io.excel.xls.w

end date: 2010-08-06
 datos desde archivo
Coefficients: 
 [-0.01007184]
Independent term: 
 6.557720079879642
Coefficients: 
 [-0.01007184]
Independent term: 
 6.557720079879642
DataFrame is empty!
  instrumento  long_short_out       date   precio
0      IBE.MC               0 2021-06-28   9.3340
1      ACX.MC               1 2021-09-22  10.9200
2      SAN.MC               1 2021-09-22   2.8995
3      TEF.MC               1 2021-09-22   4.0520
4      MTS.MC               1 2021-09-22  24.6700
5      MAP.MC               1 2021-09-22   1.7740
6     BBVA.MC               1 2021-09-22   5.2810
.............Analizando, muestra 13 fecha 2010-08-06
end date: 2010-08-07
..............Día sin sesión, next please
end date: 2010-08-08
..............Día sin sesión, next please
end date: 2010-08-09
 datos desde archivo
Coefficients: 
 [-0.00991849]
Independent term: 
 6.5500015329701435
Coefficients: 
 [-0.00991849]
Independent term: 
 6.5500015329701435
DataFrame is empty!
  instrumento  long_sho

...

  instrumento  long_short_out       date   precio
0      IBE.MC               1 2021-06-28  10.3550
1      ACX.MC               1 2021-09-22  10.9200
2      SAN.MC               1 2021-09-22   2.8995
3      TEF.MC               1 2021-09-22   4.0520
4      MTS.MC               1 2021-09-22  24.6700
5      MAP.MC               1 2021-09-22   1.7740
6     BBVA.MC               1 2021-09-22   5.2810
.............Analizando, muestra 4134 fecha 2021-11-17
end date: 2021-11-18
..............Día sin sesión, next please
end date: 2021-11-19
..............Día sin sesión, next please
end date: 2021-11-20
..............Día sin sesión, next please
end date: 2021-11-21
..............Día sin sesión, next please
end date: 2021-11-22
..............Día sin sesión, next please
end date: 2021-11-23
..............Día sin sesión, next please
end date: 2021-11-24
..............Día sin sesión, next please
end date: 2021-11-25
..............Día sin sesión, next please
end date: 2021-11-26
..............Día si

end date: 2022-08-30
..............Día sin sesión, next please
end date: 2022-08-31
..............Día sin sesión, next please
end date: 2022-09-01
..............Día sin sesión, next please
end date: 2022-09-02
..............Día sin sesión, next please
end date: 2022-09-03
..............Día sin sesión, next please
end date: 2022-09-04
..............Día sin sesión, next please
end date: 2022-09-05
..............Día sin sesión, next please
end date: 2022-09-06
..............Día sin sesión, next please
end date: 2022-09-07
..............Día sin sesión, next please
end date: 2022-09-08
..............Día sin sesión, next please
end date: 2022-09-09
..............Día sin sesión, next please
end date: 2022-09-10
..............Día sin sesión, next please
end date: 2022-09-11
..............Día sin sesión, next please
end date: 2022-09-12
..............Día sin sesión, next please
end date: 2022-09-13
..............Día sin sesión, next please
end date: 2022-09-14
..............Día sin sesión, next

end date: 2023-11-11
..............Día sin sesión, next please
end date: 2023-11-12
..............Día sin sesión, next please
end date: 2023-11-13
..............Día sin sesión, next please
end date: 2023-11-14
..............Día sin sesión, next please
end date: 2023-11-15
..............Día sin sesión, next please
end date: 2023-11-16
..............Día sin sesión, next please
end date: 2023-11-17
..............Día sin sesión, next please
end date: 2023-11-18
..............Día sin sesión, next please
end date: 2023-11-19
..............Día sin sesión, next please
end date: 2023-11-20
..............Día sin sesión, next please
end date: 2023-11-21
..............Día sin sesión, next please
end date: 2023-11-22
..............Día sin sesión, next please
end date: 2023-11-23
..............Día sin sesión, next please
end date: 2023-11-24
..............Día sin sesión, next please
end date: 2023-11-25
..............Día sin sesión, next please
end date: 2023-11-26
..............Día sin sesión, next

end date: 2025-03-09
..............Día sin sesión, next please
end date: 2025-03-10
..............Día sin sesión, next please
end date: 2025-03-11
..............Día sin sesión, next please
end date: 2025-03-12
..............Día sin sesión, next please
end date: 2025-03-13
..............Día sin sesión, next please
end date: 2025-03-14
..............Día sin sesión, next please
end date: 2025-03-15
..............Día sin sesión, next please
end date: 2025-03-16
..............Día sin sesión, next please
end date: 2025-03-17
..............Día sin sesión, next please
end date: 2025-03-18
..............Día sin sesión, next please
end date: 2025-03-19
..............Día sin sesión, next please
end date: 2025-03-20
..............Día sin sesión, next please
end date: 2025-03-21
..............Día sin sesión, next please
end date: 2025-03-22
..............Día sin sesión, next please
end date: 2025-03-23
..............Día sin sesión, next please
end date: 2025-03-24
..............Día sin sesión, next

..............Día sin sesión, next please
end date: 2026-06-05
..............Día sin sesión, next please
end date: 2026-06-06
..............Día sin sesión, next please
end date: 2026-06-07
..............Día sin sesión, next please
end date: 2026-06-08
..............Día sin sesión, next please
end date: 2026-06-09
..............Día sin sesión, next please
end date: 2026-06-10
..............Día sin sesión, next please
end date: 2026-06-11
..............Día sin sesión, next please
end date: 2026-06-12
..............Día sin sesión, next please
end date: 2026-06-13
..............Día sin sesión, next please
end date: 2026-06-14
..............Día sin sesión, next please
end date: 2026-06-15
..............Día sin sesión, next please
end date: 2026-06-16
..............Día sin sesión, next please
end date: 2026-06-17
..............Día sin sesión, next please
end date: 2026-06-18
..............Día sin sesión, next please
end date: 2026-06-19
..............Día sin sesión, next please
end date: 202

In [ ]:
dff.loc['2010':'2022','Senal'].plot(title = 'Señales Regresión a la media ' +instrumento,xlim=('2010','2022'))

In [ ]:
tiempo_final = time() 
 
tiempo_ejecucion = tiempo_final - tiempo_inicial
 
print ('El tiempo de ejecucion fue:',tiempo_ejecucion) #En segundos

In [ ]:
dff.loc['2011-01-04':'2019-11-04']

In [ ]:
#Guardamos el resultado del analisis en un pickle
dff.to_pickle("./primerBack_IBE.pkl")

Como lo que nos interesa es su cruce, para saber cuando se produce calcularemos la diferencia entre ambas medias para cada muestra. Y el signo de la diferencia será la señal para establecer la posición del sistema.

Así cuando la diferencia sea positiva, significará que la media de 20 periodos es mayor que la de 60 periodos, indicando una tendencia alcista y tomando una posición compradora. Con una diferencia negativa, la lógica es justo la inversa y tomaremos posicion vendedora.

In [ ]:
data['Dif_SMA'] = data.SMA_20 - data.SMA_60
data['Senal'] = np.sign(data.Dif_SMA)

Para calcular los retornos del sistema, calculamos la diferencia relativativa entre el precio de cierre y el del día anterior. Para posteriormente multiplicarlo por la señal que del día anterior que nos indicaba la posición a tomar.

In [ ]:
data['Dif_Close'] = data.Close.pct_change()  #calula el incremento porcentual desde la celda del dia anterior

data['Retornos'] = data.Dif_Close * data.Senal.shift(1)

In [ ]:
data.tail()

El capital, por comodidad, lo calcularemos en base 100, es decir como si iniciaramos la inversión con 100 unidades monetarias. Para su calculo arrastramos el producto acumulado de los retornos mas 1, multiplicados como dijimos por 100.

In [ ]:
data['Capital'] = (data.Retornos + 1).cumprod() * 100

Veamos como queda la tabla, tras añadir estas columnas.

Observamos de la fila 58 en adelante, pues hasta que no existen 60 filas no es posible calcular el SMA_60, y por tanto no tenemos señal para tomar posición.

In [ ]:
data[:100]

Veamos gráficamente como evoluciona el precio y las dos medias.

In [ ]:
data[['Close','SMA_20','SMA_60']].plot(color=['0.7','r','g'])
plt.show()

Pero para observar gráficamente la evolución del sistema necesitamos un gráfico con mas información. Para ello definimos una función que nos mostrará un gráfico con la evolución de nuestra estrategia, comparandola con la del activo. En un subgráfico se visualizará el drawdown del sistema, comparado de nuevo con el del activo. Y por útlimo las posiciones que toma el sistema.

In [ ]:
def grafico (df):
    estudio = df.copy()
    DD_bh, maxDD, maxDD_ini, maxDD_fin = analisis.DrawDown(estudio.Dif_Close[60:], info = False) 
    DD, maxDD, maxDD_ini, maxDD_fin = analisis.DrawDown(estudio.Retornos.fillna(0), info = False) 

    fig, (ax1, ax2, ax3) = plt.subplots(3, 1, sharex=True, figsize=(18, 12), gridspec_kw = {'height_ratios':[3, 1, 1]})
    fig.suptitle('Estrategia vs B & H', fontsize=20)

    ax1.plot(estudio.Capital.fillna(100))
    ax1.plot((estudio.Close) *100 / estudio.Close[0])
    ax1.set_title('Capital')
    ax1.legend(['Estrategia','Buy & Hold'])

    ax2.plot(DD*100, c='0.5')
    ax2.plot(DD_bh*100, c='y')
    ax2.fill_between(DD.index, 0, DD*100, color='0.7')
    ax2.set_title('Drawdown')
    ax2.legend(['Estrategia','Buy & Hold'])

    ax3.plot(estudio.Senal, c='orange')
    ax3.fill_between(estudio.index, 0, estudio.Senal*100, color='orange')
    ax3.set_title('Posición')

    plt.show()
    return

In [ ]:
grafico(data)

---

In [ ]:
data['Dif_Open'] = data.Close.pct_change()
data['Posicion'] = data.Senal.shift(1)
data['Retornos'] = data.Posicion.shift(1) * data.Dif_Open
data['Capital'] = (data.Retornos.fillna(0) + 1).cumprod() * 100

In [ ]:
data[55:70]

In [ ]:
fig, (ax1, ax2) = plt.subplots(2, 1, sharex=True, figsize=(18, 12), gridspec_kw = {'height_ratios':[3, 1]})
ax1.plot(data.Capital)
ax1.plot(data.Close *100 / data.Close[0])
ax1.set_title('Estrategia vs B & H')
ax1.legend(['Estrategia','Buy & Hold'])
ax2.plot(data.Posicion, c='y')
ax2.fill_between(data.index, 0, data.Posicion*100, color='y')
ax2.set_title('Posición')
plt.show()

---

# ANALISIS DEL SISTEMA

In [ ]:
Beneficio_Bruto = data.Capital[-1] - data.Capital[0]
print ('Beneficio Bruto : {:.2f}'.format(Beneficio_Bruto))

In [ ]:
CAGR = analisis.CAGR(data.Retornos)
print ('CAGR : {:.2f}%'.format(CAGR * 100))

In [ ]:
DD, maxDD, maxDD_ini, maxDD_fin = analisis.DrawDown(data.Retornos) 


In [ ]:
Sharpe = CAGR / (np.log(data.Retornos + 1).std(skipna=True) * 252 ** 0.5)
print ('Sharpe : {:.3f}'.format(CAGR ))

--------------------------------------------------------------------

---------------------------------------------------------------

---

# OPTIMIZACION DEL SISTEMA

In [ ]:
op_data = qd_data[:'2016'].copy()
op_data['Dif_Close'] = op_data.Close.pct_change()
op_data['Dif_Open'] = op_data.Close.pct_change()  #era Open

In [ ]:
def estrategia_medias (df, periodo_rapido, periodo_lento):
    
    estr = df.copy()
    estr[f'SMA_{periodo_rapido}'] = estr.Close.rolling(periodo_rapido).mean()
    estr[f'SMA_{periodo_lento}'] = estr.Close.rolling(periodo_lento).mean()
    estr['Dif_SMA'] = estr[f'SMA_{periodo_rapido}'] - estr[f'SMA_{periodo_lento}']    
    estr['Senal'] = estr.Dif_SMA / estr.Dif_SMA.abs()
    estr['Posicion'] = estr.Senal.shift(1)    
    estr['Retornos'] = estr.Posicion.shift(1) * estr.Dif_Open    
    estr['Capital'] = (estr.Retornos+1).cumprod() * 100
    
    resultados = {'Rapida' : periodo_rapido, 'Lenta' : periodo_lento}
    resultados['Beneficio Bruto'] = round(estr.Capital[-1]-100,2)
    resultados['CAGR'] = analisis.CAGR(estr.Retornos) 
    resultados['Sharpe'] = resultados['CAGR'] / (np.log(estr.Retornos + 1).std(skipna=True) * 252 ** 0.5)
    resultados['Máximo Drawdown'] = (estr.Capital.div(estr.Capital.cummax()).sub(1)).min()
    
    resultados['Número de trades'] = (np.sign(estr.Posicion * estr.Posicion.shift(1)) == -1).sum() 
    
    return estr, resultados

In [ ]:
periodos_rapido = range (5,160,5)
periodos_lento = range (20,210,5)


In [ ]:
%%time

coleccion = {}
resultados = {}

for periodo_rapido in periodos_rapido:
    for periodo_lento in periodos_lento:

        
        if periodo_lento <= periodo_rapido:
            continue
        estr, resultado = estrategia_medias (op_data, periodo_rapido, periodo_lento)
        nombre = f'estrategia_{periodo_rapido}_{periodo_lento}'
        coleccion[nombre] = estr
        resultados[nombre] = resultado


In [ ]:
print ('Realizados {} backtests sobre una serie de {} muestras'.format(len(coleccion), op_data.shape[0]))

In [ ]:
clasificacion = pd.DataFrame(resultados).transpose()
clasificacion.head(25)

In [ ]:
pd.DataFrame(clasificacion['Beneficio Bruto'].sort_values(ascending=False).head(10))

In [ ]:
pd.DataFrame(clasificacion.Sharpe.sort_values(ascending=False).head(10))

In [ ]:
pd.DataFrame(clasificacion['Máximo Drawdown'].sort_values(ascending=False).head(10))

In [ ]:
clasificacion['Beneficio Bruto'].sort_values(ascending=False).plot(kind='bar')

In [ ]:
(clasificacion['Beneficio Bruto']/clasificacion['Número de trades']).sort_values(ascending=False).plot(kind='bar')

In [ ]:
ax=sns.heatmap(clasificacion.pivot('Rapida','Lenta','Máximo Drawdown'), annot=False, fmt=".3", linewidths=0, cmap=plt.cm.jet)

In [ ]:
# ax=sns.heatmap(clasificacion.pivot('Rapida','Lenta','Sharpe'), annot=True, fmt=".3f", cmap=plt.cm.jet)
ax=sns.heatmap(clasificacion.pivot('Rapida','Lenta','Sharpe'), annot=False, fmt=".1f", cmap=plt.cm.jet )

In [ ]:
analisis.trisurf_heatmap (clasificacion, 'Rapida', 'Lenta','Sharpe', v1=45, v2=45)

In [ ]:
analisis.trisurf_heatmap (clasificacion, 'Rapida', 'Lenta','Máximo Drawdown',v1= 45, v2=45)

---

# REVISIÓN DE LOS PARÁMETROS SELECCIONADOS

In [ ]:
pd.DataFrame(clasificacion.loc['estrategia_5_140'])

In [ ]:
grafico(coleccion['estrategia_5_140'])


---


# PRUEBA FUERA DE LA MUESTRA

In [ ]:
periodo_rapido = 5

periodo_lento = 140

out_sample= qd_data[data.shape[0]:].copy()

out_sample['Dif_Close'] = out_sample.Close.pct_change()
out_sample['Dif_Open'] = out_sample.Close.pct_change()  #era Cloe


out_estr, out_resultado = estrategia_medias (out_sample, periodo_rapido, periodo_lento)


In [ ]:
grafico(out_estr)

---